In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.animation import FFMpegWriter

In [2]:
%config InlineBackend.figure_format = 'retina'
%matplotlib osx

In [3]:
# speed_multiplier: speed up saved file
# source_function: returns source value at given time and position
# c_matrix: matrix of speed of sound at any given position, allows for different mediums
def run_simulation(filename, speed_multiplier, source_function, c_matrix, L, N, t, dt):
    writer = FFMpegWriter(fps=15, bitrate=200000)
    fig = plt.figure(dpi=200)
    
    with writer.saving(fig, filename, dpi=200):
        # initialize grid
        X = np.linspace(0, L, N + 1)
        Y = np.linspace(0, L, N + 1)
        X, Y = np.meshgrid(X, Y)

        # initial acoustic pressures
        P = np.zeros((N + 1, N + 1)) # current values
        P_old = np.copy(P) # values one time step before

        dx = L / N
        iterations = int(t // dt)
        for it in range(iterations):
            curr_t = it * dt
            P_new = np.copy(P)
            for i in range(1, len(P) - 1):
                for j in range(1, len(P[i]) - 1):
                    i_component = P[i+1, j] - 2*P[i, j] + P[i-1, j]
                    j_component = P[i, j+1] - 2*P[i, j] + P[i, j-1]
                    P_new[i, j] = dt**2 / dx**2 * c_matrix[i, j]**2 * (i_component + j_component) + 2*P[i, j] - P_old[i, j] + dt ** 2 * source_function(i, j, curr_t)
            P_old = P
            P = P_new
            fig.clear()
            ax = fig.gca(projection='3d')
            ax.set_zlim(-10, 10)
            ax.plot_surface(X, Y, P, cmap=cm.coolwarm, antialiased=False)
            plt.draw()
            plt.pause(0.0001)
            if it % speed_multiplier == 0:
                writer.grab_frame()

In [4]:
L = 100 # length of X and Y dimensions (m)
N = 100 # number of discrete segments in each direction
t = 0.5 # length of simulation (s)
dt = 0.001 # change in time per iteration (s)

In [5]:
# single sine wave at center
def source_sin_center(i, j, t):
    if i == N // 2 and j == N // 2:
        return 10 ** 6 * np.sin(40 * t * np.pi)
    return 0
# medium is all air
air_matrix = np.full((N + 1, N + 1), 343)

run_simulation('animation1.mp4', 1, source_sin_center, air_matrix, L, N, t, dt)

In [6]:
# random
num_waves = 3
random_location = lambda: (np.random.randint(int(0.1 * N), int(0.9 * N)), np.random.randint(int(0.1 * N), int(0.9 * N)))
wave_locations = np.array([random_location() for _ in range(num_waves)])
random_amplitude = lambda: np.random.uniform(0.25, 2.0) * 10 ** 6
wave_amplitudes = np.array([random_amplitude() for _ in range(num_waves)])
print(wave_locations)
def source_random(i, j, t):
    for index in range(len(wave_locations)):
        location = wave_locations[index]
        if location[0] == i and location[1] == j:
            return wave_amplitudes[index] * np.sin(40 * t * np.pi)
    return 0

run_simulation('animation2.mp4', 1, source_random, air_matrix, L, N, t, dt)

[[40 89]
 [66 41]
 [12 38]]


In [7]:
# single sine wave at center
def source_sin_center_larger(i, j, t):
    if i == N // 2 and j == N // 2:
        return 10 ** 7 * np.sin(40 * t * np.pi)
    return 0

# water
water_matrix = np.full((N + 1, N + 1), 1480)
dt = 0.001 / 3
run_simulation('animation3.mp4', 3, source_sin_center_larger, water_matrix, L, N, t, dt)